In [1]:
print('begin')
scale_cadence = 3

begin


In [2]:
import pandas as pd
from datetime import datetime,timedelta
import numpy as np


spire_sats = [
#               '104',     # ends at 2022-06-26 01:49:00
#               '106',     # ends at 2022-06-13 06:01:17
              '113',     # ends at 2022-06-29 21:57:01
             ]

In [3]:
from pygeodyn.PYGEODYN import Pygeodyn
import datetime


scaling_cadence = 3
scale_cadence = scaling_cadence
index_buffarc_start = 0
run_list = [
#                 'jb2008',
                'msis2',
#                 'dtm2020_o',
#                 'hasdm_oc',
           ]

month_list = ['jun']

dir_modeldat='/data/SatDragModelValidation/data/inputs/atmos_models'
run_dict={}
for i in run_list:
    if i =='msis2':
        run_dict[i]={}
        run_dict[i]['num'] = 5
        run_dict[i]['model_path'] = None
    if i =='dtm2020_o':
        run_dict[i]={}
        run_dict[i]['num'] = 3
        run_dict[i]['model_path'] = None
    if i =='jb2008':
        run_dict[i]={}
        run_dict[i]['num'] = 1
        run_dict[i]['model_path'] = None
    if i =='hasdm_oc':
        run_dict[i]={}
        run_dict[i]['num'] = 2 
        run_dict[i]['model_path'] = dir_modeldat+'/hasdm/sethasdm_orbitclouds' #HASDM_OrbitCloud_2018313.01.csv
            
print(run_dict)

{'msis2': {'num': 5, 'model_path': None}}


In [4]:
def setsettings(den, SAT, run_dict, scaling_cadence, file_raw_ICs, file_g2b, input_arcs, input_epochstart, input_epochstop, scaleparameter_times):
    
    settings_spire= {# Basic input settings
             'satellite'      : {'input': 'spire'+str(SAT)},
             'den_model'      : {'input': den},
             'run_type'       : {'input': 'DataReduction_PCE'},
             'run_specifier'  : {'input': '_'},
             'cd_model'       : {'input': 'DRIA'},
             'file_string'    : {'input': 'DRIAscaled_'},
             'model_data_path' : {'input': run_dict[den]['model_path']},
             # Force Model settings
              'cd_type'               : {'input':"Fixed_CD"},
              'cd_value'              : {'input':1.0 },
              'scaling_factor'        : {'input':True},
              'hours_between_cd_adj'  : {'input':scaling_cadence},
              #### Comment for unadjusted run:
              'cd_adjustment_boolean' : {'input':True },
            #### DRIA CD Model Parameters
            'cd_model_params' : {'input':{ 
                    'MS'     : '26.980D0'   ,  #!  molar mass for each panel (g/mol)
                    'TW'     : '300.0D0'    ,  #!  temperature of panels  (K)
                    ###  Alpha is b/w 0 and 1
                    'ALPHA'  : '0.890D0'    ,  #!  accomodation coefficient
                    'KL'     : '0.0D0'    ,    #!  langmuir parameter
                    'FRACOX' : '1.0D0'   ,     #!  fraction of surface covered by atomic oxygen
               }},
              #### ---------------------------------------
             # Run
              'arc_type'       : {'input':'Nominal30hr_and_AB'},      
              'step'           : {'input': 10},
              'orbfil_step'    : {'input': 120.},
              'which_ICfile'   : {'input':file_raw_ICs},
              'which_g2bfile'  : {'input':file_g2b},
                #
              'arc'            : {'input': input_arcs},
              'epoch_start'    : {'input': input_epochstart},
              'epoch_stop'     : {'input': input_epochstop},  
        'scaleparameter_times' : {'input': scaleparameter_times},  
               #                                
              'global_options' : {'input':'pso_2018'},
             # Request read on raw outputs
              'request_data'   : {'input': ['Trajectory_orbfil', 
                                           'Density', 
                                           'Residuals_summary',
                                           'DragFile',
                                           'AdjustedParams'
                                           ]},
    }
    return(settings_spire)


In [5]:
%load_ext autoreload
%autoreload 2
from gc import collect as gc_collect
import pickle 
import os
from datetime import datetime,timedelta






##########  FIND AND FIX EPOCHS ##########
EPOCHS = {}
for sat in spire_sats:
    
    g2b_path = f"/data/SatDragModelValidation/data/inputs/sat_spire{sat}/g2b/"
    dir_save    =  f'/data/SatDragModelValidation/data/outputs_clean/spire{sat}/'

    
    if sat=='104':
        timestart = pd.to_datetime('2022-06-03 00:00:00', format='%Y-%m-%d %H:%M:%S')
        timeend   = pd.to_datetime('2022-06-25 00:00:00', format='%Y-%m-%d %H:%M:%S')
        #
        file_raw_ICs = f"{g2b_path}Spire{sat}_RawEphem_20220529_20220703.txt"
        file_g2b     = f"pce_spire{sat}_pso_20220529_20220703"

        
    elif sat=='106':
        timestart = pd.to_datetime('2022-06-04 00:00:00', format='%Y-%m-%d %H:%M:%S')
        timeend   = pd.to_datetime('2022-06-12 00:00:00', format='%Y-%m-%d %H:%M:%S')
        #
        file_raw_ICs = f"{g2b_path}Spire{sat}_RawEphem_20220603_20220629.txt"
        file_g2b     = f"pce_spire{sat}_pso_20220603_20220629"

    elif sat=='113':
        timestart = pd.to_datetime('2022-06-05 00:00:00', format='%Y-%m-%d %H:%M:%S')
        timeend   = pd.to_datetime('2022-06-28 00:00:00', format='%Y-%m-%d %H:%M:%S')
        #
        file_raw_ICs = f"{g2b_path}Spire{sat}_RawEphem_20220603_20220629.txt"
        file_g2b     = f"pce_spire{sat}_pso_20220603_20220629"

    else:
        break
        
#     print(f'Satellite FM{sat}')
#     EPOCHS[sat] = {}
#     arcs_yyyyddd = []
#     epochstart   = []
#     epochstop    = []

#     itime = timestart
#     while itime < timeend:

#         itime_0 = itime
#         itime = itime + pd.to_timedelta(24,'h')

#         arcs_yyyyddd.append(itime_0.strftime('%Y.%j'))
#         epochstart.append(itime_0.strftime('%Y-%m-%d %H:%M:%S'))
#         epochstop.append(itime.strftime(  '%Y-%m-%d %H:%M:%S'))

#     input_arcs       = []
#     input_epochstart = []
#     input_epochstop  = []
#     arc_length = []
#     scaleparameter_times = []

#     for i,val in enumerate(arcs_yyyyddd):
#         itime0 = pd.to_datetime(epochstart[i]) - pd.to_timedelta(3,'h')
#         itime1 = pd.to_datetime(epochstop[i]) + pd.to_timedelta(3,'h')
#         input_epochstart.append(itime0.strftime('%Y-%m-%d %H:%M:%S'))
#         input_epochstop.append(itime1.strftime('%Y-%m-%d %H:%M:%S'))
#         epoch_delta  =  pd.to_timedelta(pd.to_datetime(itime1) - pd.to_datetime(itime0), 'hours')
#         arc_length.append(epoch_delta.total_seconds()/3600)

#     ### Use Arc text file times
#         input_arcs.append(      arcs_yyyyddd[i])
#         scalestart = str(pd.to_datetime(arcs_yyyyddd[i],format="%Y.%j"))
#         scalestop  = str(pd.to_datetime(arcs_yyyyddd[i],format="%Y.%j") + pd.to_timedelta(24,'h'))
#         scaletimes = pd.date_range(start = pd.to_datetime(scalestart),
#                                                   end   = pd.to_datetime(scalestop ),
#                                                   freq=str(scale_cadence)+"h")
#         ###append the epoch end time to the end
#         add_epochend = np.append(scaletimes.values.astype(np.int64) // 10 ** 9,
#                       pd.to_datetime(pd.Series(itime1)).values.astype(np.int64) // 10 ** 9)
#         scaleparameter_times.append([pd.to_datetime(datetime.strftime(datetime.fromtimestamp(ts), '%y%m%d%H%M%S.%f'),
#             format ='%y%m%d%H%M%S.%f' )
#                          for ts in add_epochend ])
        
#     #### Update the start time to match those in the file
#     ### For each starting time, be sure that the time exists in the Initial Conditions file.
#     ### If not, choose the closest time BEFORE, or report if its longer than ~2 hours away.
#     PCE_data_raw = pd.read_csv(file_raw_ICs, 
#                 skiprows = 23, 
#                 sep = r"\s+",
#                 names = ['DateYMD','DateHMS','X_pce','Y_pce','Z_pce','Xdot_pce','Ydot_pce','Zdot_pce'],)
#     PCE_data_raw['Date_pd'] =  pd.to_datetime(PCE_data_raw['DateYMD']+PCE_data_raw['DateHMS'],\
#                                         format='%Y-%m-%d%H:%M:%S')
#     del PCE_data_raw['DateYMD'], PCE_data_raw['DateHMS']
#     del PCE_data_raw['X_pce'], PCE_data_raw['Y_pce'], PCE_data_raw['Z_pce']
#     del PCE_data_raw['Xdot_pce'], PCE_data_raw['Ydot_pce'], PCE_data_raw['Zdot_pce']

#     def nearest(items, pivot):
#         return min(items, key=lambda x: abs(x - pivot))

#     update_starts = []
#     for i,val in enumerate(input_epochstart):

#         date_near = nearest(PCE_data_raw['Date_pd'], pd.to_datetime(val))
#         print(f"Updating {val} to {date_near}")
        
#         if np.abs(pd.to_datetime(val) - date_near).total_seconds()/60/60  > 2:
#             print(' -- difference bigger than 2 hours, index', i)
            
#         update_starts.append(date_near.strftime('%Y-%m-%d %H:%M:%S'))
#     #     indx = np.where(pd.to_datetime(PCE_data_raw['Date_pd']) == pd.to_datetime(date_near))[0][0]

#     input_epochstart = update_starts

#     if sat=='113':
#         del input_arcs[3]
#         del input_epochstart[3]
#         del input_epochstop[3]
#         del scaleparameter_times[3]

#         del input_arcs[18-1]
#         del input_epochstart[18-1]
#         del input_epochstop[18-1]
#         del scaleparameter_times[18-1]
        
#     del PCE_data_raw
    ################################################################################

    SAT = sat
    obj = {}

#     for i,den in enumerate(run_list):
#         settings_spire = setsettings(den,SAT, run_dict, scaling_cadence, file_raw_ICs, file_g2b, 
#                                      input_arcs, 
#                                      input_epochstart, 
#                                      input_epochstop, 
#                                      scaleparameter_times)
#         sat = Pygeodyn(settings_spire, use_file=False)
#         sat.run_arcs()
#         gc_collect()

        
#     for i,den in enumerate(run_list):
#         settings_spire = setsettings(den,SAT, run_dict, scaling_cadence, file_raw_ICs, file_g2b, 
#                                      input_arcs, 
#                                      input_epochstart, 
#                                      input_epochstop, 
#                                      scaleparameter_times)
#         sat = Pygeodyn(settings_spire, use_file=False)
#         obj[den] =  sat.getData_BigData_lowmemory(orbit_propagation=False)
#         obj[den] = vars(obj[den])
#         gc_collect()

        
    for i,den in enumerate(run_list):
        pickleName = f'_DRIA_scale{scale_cadence}.pkl'

        pickle_file = dir_save+den+pickleName
        if not os.path.exists(pickle_file):
            print('Must create pickle file...')
            print('   ',  pickle_file)
            print('   ', 'Reading Geodyn Data')

            ### Load the data into an object
            settings_spire = setsettings(den,SAT, run_dict, scaling_cadence, file_raw_ICs, file_g2b, 
                                         input_arcs, 
                                         input_epochstart, 
                                         input_epochstop, 
                                         scaleparameter_times)
            sat = Pygeodyn(settings_spire, use_file=False)
            obj = sat.getData_BigData_lowmemory(orbit_propagation=False)
            gc_collect()

            #### Pickle the object to save it
            print('   ', 'Saving pickle')
            filehandler = open(pickle_file, 'wb') 
            pickle.dump(vars(obj), filehandler)
            filehandler.close()
            obj = 0
            print('   ', 'Saved pickle')

    obj = {}
    for i,model in enumerate(run_list):
        pickleName = f'_DRIA_scale{scale_cadence}.pkl'

        ### Load the data if the pickles exist
        print()
        print()
        gc_collect()

        pickle_file = dir_save+model+pickleName

        obj[model] = pd.read_pickle(pickle_file)
    #         filehandler = open(pickle_file, 'rb') 
    #         obj[month+model] = pickle.load(filehandler)
    #         filehandler.close()
        print('Loaded data from pickle... ',  model)

    ### Save space if doing density retrieval
    for model in run_dict.keys():
        del obj[model]['OrbitResids']
        del obj[model]['Trajectory_orbfil']

    gc_collect()





Loaded data from pickle...  msis2


In [6]:
def plot_cleanformat_axes(fig, font_dict):
    rownum, colnum = fig._get_subplot_rows_columns()

    for i in rownum:
        if len(rownum)==1:
            L_ticklabel = True
        else:
            if i < len(rownum):
                L_ticklabel = False
            else:
                L_ticklabel = True
        fig.update_xaxes(### LINE at axis border
                          showline=True,
                          showticklabels=L_ticklabel,
    #                       tickformat= '%m/%d',
                          linecolor='black',
                          linewidth=1,
                         ### Major ticks
                          ticks='inside',
                          tickfont=font_dict,
                          mirror=True,
    #                       tickwidth=2,
    #                       ticklen=9,
                          tickcolor='grey',
    #                       tick0="2018-11-9" ,
    #                       dtick=86400000.0*1,    # milliseconds in a day, every 7 days
                          #### Minor Ticks
                           minor=dict(
                             dtick=86400000.0, # milliseconds in a day
                             tickwidth=1,
                             ticklen=4,
                             tickcolor='grey',
                             ticks='inside'),
                          ### GRID
                           gridcolor='gainsboro',
                           gridwidth=1,
                           layer='above traces',
                           tickangle=0,
                           row=i, col=1)
        fig.update_yaxes(showline=True,      # add line at x=0
                             showticklabels=True,
                             linecolor='black',  # line color
                             linewidth=1,        # line size
                         ticks='inside',     # ticks outside axis
                         tickfont=font_dict, # tick label font
                         mirror='allticks',  # add ticks to top/right axes
                         tickwidth=1,      # tick width
                         tickcolor='black',  # tick color
                         gridcolor='gainsboro',
                         gridwidth=1,
                         layer='above traces',
                         row=i, col=1)
    return(fig)

from pygeodyn.pygeodyn_plot_scalingfactors import *

coldict = {}
coldict['msis2']     = "#2ca02c"  # 'tab:green'
coldict['dtm2020_o'] = "#d62728"  # 'tab:red'
coldict['jb2008']    = "orange"   
coldict['hasdm_oc']  = "#1f77b4"     


# 
# run_dict={}
# for imonth,month in enumerate(month_list):
#     for i in run_list:
#         if i =='msis2':
#             run_dict[month+i]={}
#             run_dict[month+i]['num'] = 5
#             run_dict[month+i]['model_path'] = None
#         if i =='dtm2020_o':
#             run_dict[month+i]={}
#             run_dict[month+i]['num'] = 3
#             run_dict[month+i]['model_path'] = None
#         if i =='jb2008':
#             run_dict[month+i]={}
#             run_dict[month+i]['num'] = 1
#             run_dict[month+i]['model_path'] = None
#         if i =='hasdm_oc':
#             run_dict[month+i]={}
#             run_dict[month+i]['num'] = 2 
#             run_dict[month+i]['model_path'] = dir_modeldat+'/hasdm/sethasdm_orbitclouds' 
# print(run_dict)
#  


In [7]:
if int(SAT)   == 106:
    satid = 1903826
elif int(SAT) == 104:
    satid = 1903812
elif int(SAT) == 113:
    satid = 1903824   
else:
    print('Add satellite Numbers')
    import sys
    sys.exit(0)
    
wgts = {}

for model in run_dict.keys():
    wgts[model] = {}
    ScalingFactors  = []
    ScalingFactor_times = []

    for ii,arc in enumerate(obj[model]['global_params']['arc_input']):
        epochstart = obj[model]['global_params']['prms']['epoch_start'][ii]
        hrs = pd.to_datetime(epochstart, format='%Y-%m-%d %H:%M:%S').hour
        frachours =(hrs/24)
        #
        if len(arc) == 9:
            maneuv_indicator = arc[8]
        else:
            maneuv_indicator = ''
        arc_type = obj[model]['global_params']['prms']['arc_type']
        if arc_type == "Nominal30hr_and_AB":
            arc_name =arc[:8]+ maneuv_indicator
        else:
            arc_name =arc[:8]+('%.3f'%frachours).lstrip('0')+ maneuv_indicator
        ### Collect the weights for the ensemble average
        inv_rms          = 1/obj[model]['Statistics'][arc_name]['T_RMS'].values[0]
        wgts[model][arc_name] = inv_rms#/sum_wgts

        iters = int(obj[model]['run_parameters'+arc_name]['total_iterations']) 
        for iit, itime in enumerate(obj[model]['AdjustedParams'][arc_name][iters][satid]['0CD'].keys()):
            if iit == 0 or iit==9:
                pass
            else:
                CURRENT_VALUE = obj[model]['AdjustedParams'][arc_name][iters][satid]['0CD'][itime]['CURRENT_VALUE']
                APRIORI_VALUE = obj[model]['AdjustedParams'][arc_name][iters][satid]['0CD'][itime]['APRIORI_VALUE']
                ScalingFactors.append(CURRENT_VALUE/APRIORI_VALUE)
                ScalingFactor_times.append(itime)
    run_dict[model]['ScalingFactor_times'] = ScalingFactor_times
    run_dict[model]['ScalingFactors']      = ScalingFactors
    run_dict[model]['Weight'] = wgts[model]
    

    
###### SCALE THE DENSITIES:
models_dens = {}
for monthmodel in run_dict.keys():
    print(f"---Making continuous scaled rho for {monthmodel}")
    models_dens[monthmodel] = get_continuous_scaled_densities(obj, run_dict, monthmodel, scale_cadence)

    del obj[monthmodel]
    gc_collect()

del obj
gc_collect()
## Retrieve scaled ensemble weighted average
##     'Rho_x' denotes the ensemble weighted avg

# models_dens =  calc_rho_ScaledEnsembleWgtAvg(models_dens, run_dict, month_list, run_list)




---Making continuous scaled rho for msis2


0

## Correlation Plot


In [8]:
for sat in spire_sats:
    
    g2b_path = f"/data/SatDragModelValidation/data/inputs/sat_spire{sat}/g2b/"
    dir_save    =  f'/data/SatDragModelValidation/data/outputs_clean/spire{sat}/'

    
    if sat=='104':
        timestart = pd.to_datetime('2022-06-03 00:00:00', format='%Y-%m-%d %H:%M:%S')
        timeend   = pd.to_datetime('2022-06-25 00:00:00', format='%Y-%m-%d %H:%M:%S')
        #
        file_raw_ICs = f"{g2b_path}Spire{sat}_RawEphem_20220529_20220703.txt"
        file_g2b     = f"pce_spire{sat}_pso_20220529_20220703"

        
    elif sat=='106':
        timestart = pd.to_datetime('2022-06-04 00:00:00', format='%Y-%m-%d %H:%M:%S')
        timeend   = pd.to_datetime('2022-06-12 00:00:00', format='%Y-%m-%d %H:%M:%S')
        #
        file_raw_ICs = f"{g2b_path}Spire{sat}_RawEphem_20220603_20220629.txt"
        file_g2b     = f"pce_spire{sat}_pso_20220603_20220629"

    elif sat=='113':
        timestart = pd.to_datetime('2022-06-05 00:00:00', format='%Y-%m-%d %H:%M:%S')
        timeend   = pd.to_datetime('2022-06-28 00:00:00', format='%Y-%m-%d %H:%M:%S')
        #
        file_raw_ICs = f"{g2b_path}Spire{sat}_RawEphem_20220603_20220629.txt"
        file_g2b     = f"pce_spire{sat}_pso_20220603_20220629"



PCE_data_raw = pd.read_csv(file_raw_ICs, 
                skiprows = 23, 
                sep = r"\s+",
                names = ['DateYMD','DateHMS','X_pce','Y_pce','Z_pce','Xdot_pce','Ydot_pce','Zdot_pce'],)
PCE_data_raw['Date_pd'] =  pd.to_datetime(PCE_data_raw['DateYMD']+PCE_data_raw['DateHMS'],\
                                    format='%Y-%m-%d%H:%M:%S')
del PCE_data_raw['DateYMD'], PCE_data_raw['DateHMS']
# del PCE_data_raw['X_pce'], PCE_data_raw['Y_pce'], PCE_data_raw['Z_pce']
# del PCE_data_raw['Xdot_pce'], PCE_data_raw['Ydot_pce'], PCE_data_raw['Zdot_pce']


In [9]:
PCE_data_raw

X_pce         Y_pce         Z_pce    Xdot_pce    Ydot_pce  \
0       1.988312e+05  1.324541e+06  6.754948e+06  4404.37035 -6111.00564   
1       2.032354e+05  1.318429e+06  6.755994e+06  4404.12624 -6112.61010   
2       2.076394e+05  1.312315e+06  6.757031e+06  4403.87679 -6114.20714   
3       2.120432e+05  1.306200e+06  6.758061e+06  4403.62199 -6115.79677   
4       2.164467e+05  1.300084e+06  6.759081e+06  4403.36183 -6117.37898   
...              ...           ...           ...         ...         ...   
337966 -5.869678e+06  3.530625e+06  7.749271e+05  1276.53563   426.99254   
337967 -5.868398e+06  3.531050e+06  7.824140e+05  1283.68671   422.69034   
337968 -5.867110e+06  3.531471e+06  7.898999e+05  1290.83630   418.38758   
337969 -5.865816e+06  3.531887e+06  7.973849e+05  1297.98438   414.08426   
337970 -5.864515e+06  3.532299e+06  8.048688e+05  1305.13096   409.78040   

          Zdot_pce             Date_pd  
0       1049.76319 2022-06-04 22:13:34  
1       1041.53865 2022-06-04 22:13:35  
2       1033.31280 2022-06-04 22:13:36  
3       1025.08564 2022-06-04 22:13:37  
4       1016.85717 2022-06-04 22:13:38  
...            ...                 ...  
337966  7487.35660 2022-06-29 21:56:57  
337967  7486.40523 2022-06-29 21:56:58  
337968  7485.44470 2022-06-29 21:56:59  
337969  7484.47501 2022-06-29 21:57:00  
337970  7483.49617 2022-06-29 21:57:01  

[337971 rows x 7 columns]

In [10]:
import linecache
import pandas as pd
import numpy as np

path_to_flux = "/data/SatDragModelValidation/src/geodyn_code/support/geodyn_support/make_tables/"


dateS   = []
dateAP  = []
dateKP8 = []

fluxS   = []
fluxAP  = []
fluxKP8 = []

switch = 0
with open(path_to_flux+"new_master", 'r') as f:
    for line_no, string in enumerate(f):
#         string = linecache.getline("new_master",line+1) #

        if 'MASTER' in string:        
            switch = 'skip'
            continue
            
        ### Skip the title lines and any dates before Y2K
        if 'FLUXS' in string:        
            switch = 'readfluxS'
            print(switch)
            continue

        if 'FLUXAP' in string:        
            switch = 'readfluxAP'
            print(switch)
            continue
        if 'FLUXKP8' in string:        
            switch = 'readfluxKP8'
            print(switch)
            continue

        if switch =='skip':
            continue
            
        if int(string[:2]) >= 58:
            continue
        else:
            
            if int(string[:2]) < 22 or int(string[:2]) > 22:
                continue
                
            if switch == 'readfluxS':
                ### Load the Solar Flux values after 2000. The date leading each line represents
                ### the first flux value in that line.  The following n values are that day + n days.
                ###  All Solar Flux values are mulitplied by 10 for some reason...

                for n in range(0,12):
                    dateS.append(pd.to_datetime(string[:6],format='%y%m%d') + n*pd.to_timedelta(1,'d') )
                fluxS.append(int(string[11:15]) / 10)
                fluxS.append(int(string[16:20]) / 10)
                fluxS.append(int(string[21:25]) / 10)
                fluxS.append(int(string[26:30]) / 10)
                fluxS.append(int(string[31:35]) / 10)
                fluxS.append(int(string[36:40]) / 10)
                fluxS.append(int(string[41:45]) / 10)
                fluxS.append(int(string[46:50]) / 10)
                fluxS.append(int(string[51:55]) / 10)
                fluxS.append(int(string[56:60]) / 10)
                fluxS.append(int(string[61:65]) / 10)
                fluxS.append(int(string[66:70]) / 10)

            if switch == 'readfluxAP':
                ### Load the AP values after 2000. These are formatted the same as the FLUXS section
                for n in range(0,12):
                    dateAP.append(pd.to_datetime(string[:6],format='%y%m%d') + n*pd.to_timedelta(1,'d') )
                fluxAP.append(int(string[11:15]) / 10)
                fluxAP.append(int(string[16:20]) / 10)
                fluxAP.append(int(string[21:25]) / 10)
                fluxAP.append(int(string[26:30]) / 10)
                fluxAP.append(int(string[31:35]) / 10)
                fluxAP.append(int(string[36:40]) / 10)
                fluxAP.append(int(string[41:45]) / 10)
                fluxAP.append(int(string[46:50]) / 10)
                fluxAP.append(int(string[51:55]) / 10)
                fluxAP.append(int(string[56:60]) / 10)
                fluxAP.append(int(string[61:65]) / 10)
                fluxAP.append(int(string[66:70]) / 10)

            if switch == 'readfluxKP8':
                ### Load the KP values after 2000. These are formatted such that each line is a day
                ### and each nth value in the line is n*3hrs for the day
                for n in range(0,8):
                    dateKP8.append(pd.to_datetime(string[:6],format='%y%m%d') + n*pd.to_timedelta(3,'h') )
                fluxKP8.append(int(string[7:11])  / 100)
                fluxKP8.append(int(string[12:16]) / 100)
                fluxKP8.append(int(string[17:21]) / 100)
                fluxKP8.append(int(string[22:26]) / 100)
                fluxKP8.append(int(string[27:31]) / 100)
                fluxKP8.append(int(string[32:36]) / 100)
                fluxKP8.append(int(string[37:41]) / 100)
                fluxKP8.append(int(string[42:46]) / 100)

fluxS = np.array(fluxS)
fluxAP = np.array(fluxAP)
fluxKP8 = np.array(fluxKP8)
                
fluxS   = np.where(fluxS  == 0., np.nan, fluxS  )
fluxAP  = np.where(fluxAP ==0., np.nan, fluxAP )
fluxKP8 = np.where(fluxKP8==0., np.nan, fluxKP8)



readfluxS
readfluxAP
readfluxKP8


In [11]:
# dateStart = timestart.strftime('2022-06-12')
# dateStop  = timeend.strftime('2022-06-18') 
dateStart = timestart.strftime('%Y-%m-%d') 
dateStop  = timeend.strftime('%Y-%m-%d') 
# print('')

dff107 = pd.DataFrame(data={'Date':dateS, 'f107':fluxS})
dff107 = dff107.query(f"Date >= '{dateStart}' and Date < '{dateStop}'")

dfkp = pd.DataFrame(data={'Date':dateKP8,'Kp':fluxKP8})
dfkp = dfkp.query(f"Date >= '{dateStart}' and Date < '{dateStop}'")

PCE_data_raw = PCE_data_raw.query(f"Date_pd >= '{dateStart}' and Date_pd < '{dateStop}'")





# exat_data = 

In [12]:
%load_ext autoreload
%autoreload 2





def PLOT_(fig,  den_dict, model_dict, _model_name_):
    
    SHOW_alldata = True
    
    model_m1 = _model_name_#[3:]
#     print('model_m1', model_m1)





    fig.add_trace(go.Scattergl(x=pd.to_datetime(model_dict['ScalingFactor_times'])-pd.to_timedelta(scale_cadence/2, 'h'),
                           y=model_dict['ScalingFactors'],
                           name= model,
                           mode='markers',
                           opacity=1,
                           marker=dict(color=coldict[model_m1], size=5),
                           showlegend=False),
                           secondary_y=False,row=1, col=1)

    fig.add_trace(go.Scattergl(x= PCE_data_raw['Date_pd'][::20],
                               y= PCE_data_raw['Z_pce'][::20],
                               ### name= model_m1,
                               mode='markers',
                               opacity=1,
                                   marker=dict(size=1),
                                   line = dict(dash ='solid',  width=2),
                               showlegend=False), row=2, col=1)
    fig.add_trace(go.Scattergl(x= PCE_data_raw['Date_pd'][::20],
                               y= PCE_data_raw['X_pce'][::20],
                               ### name= model_m1,
                               mode='markers',
                               opacity=1,
                                   marker=dict(size=1),
                                   line = dict(dash ='solid',  width=2),
                               showlegend=False), row=2, col=1)
    fig.add_trace(go.Scattergl(x= PCE_data_raw['Date_pd'][::20],
                               y= PCE_data_raw['Y_pce'][::20],
                               ### name= model_m1,
                               mode='markers',
                               opacity=1,
                                   marker=dict(size=1),
                                   line = dict(dash ='solid',  width=2),
                               showlegend=False), row=2, col=1)

#     fig.add_trace(go.Scattergl(x= exat_data['Date'][::2],
#                                y= exat_data['qW'][::2],
#                                ### name= model_m1,
#                                mode='markers',
#                                opacity=1,
#                                    marker=dict(size=2),
#                                    line = dict(dash ='solid',  width=2),
#                                showlegend=False), row=4, col=1)
        
    return(fig)



fig = make_subplots(rows=2, cols=1, row_heights=[0.5, 0.5],#],
                    specs=[[{"secondary_y": False}],
                           [{"secondary_y": False}]],
                           shared_xaxes=True,
                           vertical_spacing=0.02)


for model in run_dict.keys():
    print('model', model)

    fig = PLOT_(fig, models_dens[model], run_dict[model], model)

    

    
#######################################################
font_dict=dict(family='Arial',size=14,color='black')
## automate the specification of the axes for subplots
fig = plot_cleanformat_axes(fig, font_dict)


fig.update_yaxes(title_text="Scaling Factor", 
                 range=[-5,10],
                 exponentformat= 'power',row=1, col=1)

fig.update_yaxes(title_text="Position (XYZ)", 
                 type="linear", 
                 exponentformat= 'power',row=2, col=1)


    
a='input'
# s=settings_spire
fig.update_layout(autosize=False,    width=450,    height=500,
                  legend= {'itemsizing': 'trace'},
                  font=font_dict,
                  plot_bgcolor='white', 
                 )
fig.update_annotations(font_size=16)  # Increase size of subplot title
# fig.show(config=config)
fig.show(config= dict({
                'displayModeBar': False,
#                 'responsive': False,
#                 'staticPlot': True,
                'responsive': True,
                'staticPlot': False,
                'displaylogo': False,
                'showTips': False,
                }),
#          renderer='jpg',
)




The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
model msis2


In [13]:
dates = pd.date_range(start=dateStart, end=dateStop)


bigdf = {}

for ifn,val in enumerate(dates):
#     print()   
    
    file_exat = f"/data/SatDragModelValidation/data/inputs/sat_spire113/external_attitude/EXAT01.{val.strftime('%Y.%j')}_check.txt"

    bigdf[ifn] = pd.read_csv(file_exat, 
                skiprows = 4, 
                sep = ",",
                names = ['Date','qX','qY','qZ','qW'],)

    bigdf[ifn]['Date'] =  pd.to_datetime(bigdf[ifn]['Date'])



exat_data = pd.concat([ bigdf[ifn] for ifn,val in enumerate(dates)]  )
exat_data = exat_data.reset_index(drop=True)
    
    
    
exat_data = exat_data.query(f"Date >= '{dateStart}' and Date < '{dateStop}'")
    



In [14]:
# exat_data

In [15]:
# %load_ext autoreload
# %autoreload 2





# def PLOT_(fig,  den_dict, model_dict, _model_name_):
    
#     SHOW_alldata = True
    
#     model_m1 = _model_name_#[3:]
# #     print('model_m1', model_m1)


#     fig.add_trace(go.Scattergl(x=dff107['Date'],
#                                y=dff107['f107'],
#                                name= 'F107d_1AU',
#                                mode='lines',
#                                opacity=1,
#                                line = dict(shape = 'hvh',dash='dash', color = 'blue', width=2),
#                                showlegend=False),
#                                secondary_y=True,row=1, col=1)

#     fig.add_trace(go.Scattergl(x=dfkp['Date'],
#                                y=dfkp['Kp'],
#                                name= 'Kp',
#                                mode='lines',
#                                opacity=1,
#                                line = dict(shape = 'hvh', color = 'black', width=2),
#                                showlegend=False),
#                                secondary_y=False,row=1, col=1) 



#     fig.add_trace(go.Scattergl(x=pd.to_datetime(model_dict['ScalingFactor_times'])-pd.to_timedelta(scale_cadence/2, 'h'),
#                            y=model_dict['ScalingFactors'],
#                            name= model,
#                            mode='markers',
#                            opacity=1,
#                            marker=dict(color=coldict[model_m1], size=5),
#                            showlegend=False),
#                            secondary_y=False,row=2, col=1)

#     fig.add_trace(go.Scattergl(x= PCE_data_raw['Date_pd'][::20],
#                                y= PCE_data_raw['Z_pce'][::20],
#                                ### name= model_m1,
#                                mode='markers',
#                                opacity=1,
#                                    marker=dict(size=2),
#                                    line = dict(dash ='solid',  width=2),
#                                showlegend=False), row=3, col=1)
#     fig.add_trace(go.Scattergl(x= PCE_data_raw['Date_pd'][::20],
#                                y= PCE_data_raw['X_pce'][::20],
#                                ### name= model_m1,
#                                mode='markers',
#                                opacity=1,
#                                    marker=dict(size=2),
#                                    line = dict(dash ='solid',  width=2),
#                                showlegend=False), row=3, col=1)
#     fig.add_trace(go.Scattergl(x= PCE_data_raw['Date_pd'][::20],
#                                y= PCE_data_raw['Y_pce'][::20],
#                                ### name= model_m1,
#                                mode='markers',
#                                opacity=1,
#                                    marker=dict(size=2),
#                                    line = dict(dash ='solid',  width=2),
#                                showlegend=False), row=3, col=1)

#     fig.add_trace(go.Scattergl(x= exat_data['Date'][::2],
#                                y= exat_data['qW'][::2],
#                                ### name= model_m1,
#                                mode='markers',
#                                opacity=1,
#                                    marker=dict(size=2),
#                                    line = dict(dash ='solid',  width=2),
#                                showlegend=False), row=4, col=1)
        
#     return(fig)



# fig = make_subplots(rows=4, cols=1, row_heights=[0.1, 0.3, 0.3, 0.3],#],
#                     specs=[[{"secondary_y": True}],
#                            [{"secondary_y": False}],
#                            [{"secondary_y": False}],
# #                            [{"secondary_y": False}],
#                            [{"secondary_y": False}]],
#                            shared_xaxes=True,
#                            vertical_spacing=0.02)


# for model in run_dict.keys():
#     print('model', model)

#     fig = PLOT_(fig, models_dens[model], run_dict[model], model)

    
# ### UPDATE AXES 
# fig.update_yaxes(title_text="Kp", 
#                  exponentformat= 'power',
# #                  range=[0,7],
#                  secondary_y=False,
#                  row=1, col=1)
# fig.update_yaxes(title_text="F10.7", 
#                  exponentformat= 'power',
#                  range=[35,170],
#                  secondary_y=True,
#                  tickfont=dict(color="blue"),
#                  titlefont=dict(color="blue"),
#                  row=1, col=1)

    
# #######################################################
# font_dict=dict(family='Arial',size=11,color='black')
# ## automate the specification of the axes for subplots
# fig = plot_cleanformat_axes(fig, font_dict)


# fig.update_yaxes(title_text="Scaling Factor", 
#                  exponentformat= 'power',row=2, col=1)

# fig.update_yaxes(title_text="XYZ  ", 
#                  type="linear", 
#                  exponentformat= 'power',row=3, col=1)
# # fig.update_yaxes(title_text="Scaled Density", 
# #                   type="log", 
# #                  exponentformat= 'power',row=4, col=1)


    
# a='input'
# # s=settings_spire
# fig.update_layout(autosize=False,    width=850,    height=900,
#                   legend= {'itemsizing': 'trace'},
#                   font=font_dict,
#                   plot_bgcolor='white', 
#                  )
# fig.update_annotations(font_size=16)  # Increase size of subplot title
# # fig.show(config=config)
# fig.show(config= dict({
#                 'displayModeBar': False,
# #                 'responsive': False,
# #                 'staticPlot': True,
#                 'responsive': True,
#                 'staticPlot': False,
#                 'displaylogo': False,
#                 'showTips': False,
#                 }),
# #          renderer='jpg',
# )




In [16]:
df = pd.DataFrame(data={'Date':dateKP8,
                        'Kp':fluxKP8,
                       })
df.query("Date >= '2022-06-04' and Date < '2022-06-12'")

Date    Kp
1232 2022-06-04 00:00:00  0.33
1233 2022-06-04 03:00:00  0.67
1234 2022-06-04 06:00:00  1.00
1235 2022-06-04 09:00:00  0.33
1236 2022-06-04 12:00:00  0.33
...                  ...   ...
1291 2022-06-11 09:00:00  1.00
1292 2022-06-11 12:00:00  1.33
1293 2022-06-11 15:00:00  1.67
1294 2022-06-11 18:00:00  1.33
1295 2022-06-11 21:00:00  1.67

[64 rows x 2 columns]

In [17]:
# res

In [18]:
len(fluxKP8)

2920

In [19]:
import sys
sys.exit(0)

SystemExit: 0

/data/miniconda3/envs/pygeodyn2/lib/python3.12/site-packages/IPython/core/interactiveshell.py:3561: UserWarning:

To exit: use 'exit', 'quit', or Ctrl-D.



In [ ]:
%load_ext autoreload
%autoreload 2


def PLOT_resids(fig,  den_dict, model_dict, _model_name_):
    
    SHOW_alldata = True
    
    model_m1 = _model_name_#[3:]
#     print('model_m1', model_m1)


    fig.add_trace(go.Scattergl(x=dateS,
                               y=fluxS,
                               name= 'F107d_1AU',
                               mode='lines',
                               opacity=1,
                               line = dict(shape = 'hvh',dash='dash', color = 'blue', width=2),
                               showlegend=False),
                               secondary_y=True,row=1, col=1)

    fig.add_trace(go.Scattergl(x=dateKP8,
                               y=fluxKP8,
                               name= 'Kp',
                               mode='lines',
                               opacity=1,
                               line = dict(shape = 'hvh', color = 'black', width=2),
                               showlegend=False),
                               secondary_y=False,row=1, col=1) 



    fig.add_trace(go.Scattergl(x=pd.to_datetime(model_dict['ScalingFactor_times'])-pd.to_timedelta(scale_cadence/2, 'h'),
                           y=model_dict['ScalingFactors'],
                           name= model,
                           mode='markers',
                           opacity=1,
                           marker=dict(color=coldict[model_m1], size=5),
#                                marker=dict(color=coldict[model_m1], 
#                                            size=6,
#                                            symbol='line-ew',
#                                            line = dict(color = coldict[model_m1], width=3)), #symbol='diamond-wide'),
#                            line = dict(shape = 'hvh',dash ='dash', color = coldict[model_m1], width=1),
                           showlegend=False),
                           secondary_y=False,row=2, col=1)

    
    
    time_avg,dscale_avg = orbit_avg_generic(den_dict['dates'], den_dict['denscaled'], den_dict['lat'])
    ## -----------------------------------------------------------------------------------------------------
#     ##     Orbit Averaged Density
    fig.add_trace(go.Scattergl(x=time_avg,
                               y=dscale_avg,
                               ### name= model_m1,
                               mode='markers+lines',
                               opacity=1,
                                   marker=dict(color=coldict[model_m1],size=2),
                                   line = dict(dash ='solid', color = coldict[model_m1], width=2),
                               showlegend=False), row=4, col=1)
#     fig.add_trace(go.Scattergl(x=den_dict['dates'],
#                                y=den_dict['denscaled'],
#                                ### name= model_m1,
#                                mode='markers+lines',
#                                opacity=1,
#                                    marker=dict(color=coldict[model_m1],size=2),
#                                    line = dict(dash ='solid', color = coldict[model_m1], width=2),
#                                showlegend=False), row=4, col=1)

    
    
    
    
    time_avg,d_avg = orbit_avg_generic(den_dict['dates'], den_dict['dens'], den_dict['lat'])
    ### -----------------------------------------------------------------------------------------------------
    ##     Orbit Averaged Density
#     fig.add_trace(go.Scattergl(x=den_dict['dates'], #time_avg,
#                                y=den_dict['dens'], #d_avg,
#                                ### name= model_m1,
#                                mode='markers+lines',
#                                opacity=1,
#                                    marker=dict(color=coldict[model_m1],size=1),
#                                    line = dict(dash ='solid', color = coldict[model_m1], width=2),
#                                showlegend=False), row=3, col=1)

    ###     Orbit Averaged Density
    fig.add_trace(go.Scattergl(x=time_avg,
                               y=d_avg,
                               ### name= model_m1,
                               mode='markers+lines',
                               opacity=1,
                                   marker=dict(color= coldict[model_m1],size=2),
                                   line = dict(dash ='solid', color = coldict[model_m1], width=2),
                               showlegend=False), row=3, col=1)
        
    return(fig)



fig = make_subplots(rows=4, cols=1, row_heights=[0.2, 0.2, 0.3, 0.3],#],
                    specs=[[{"secondary_y": True}],
                           [{"secondary_y": False}],
                           [{"secondary_y": False}],
#                            [{"secondary_y": False}],
                           [{"secondary_y": False}]],
                           shared_xaxes=True,
                           vertical_spacing=0.02)


for model in run_dict.keys():
#     for imonth,month in enumerate(month_list):
    print('model', model)

    fig = PLOT_resids(fig, models_dens[model], run_dict[model], model)

    
### UPDATE AXES 
fig.update_yaxes(title_text="Kp", 
                 exponentformat= 'power',
#                  range=[0,7],
                 secondary_y=False,
                 row=1, col=1)
fig.update_yaxes(title_text="F10.7", 
                 exponentformat= 'power',
                 range=[35,170],
                 secondary_y=True,
                 tickfont=dict(color="blue"),
                 titlefont=dict(color="blue"),
                 row=1, col=1)
fig.update_xaxes(range=[pd.to_datetime(input_epochstart[0]), pd.to_datetime(input_epochstop[-1])])




################################################################################
    
#######################################################
font_dict=dict(family='Arial',size=11,color='black')
## automate the specification of the axes for subplots
fig = plot_cleanformat_axes(fig, font_dict)


fig.update_yaxes(title_text="Scaling Factor", 
                 exponentformat= 'power',row=2, col=1)

fig.update_yaxes(title_text="Density", 
                 type="log", 
                 exponentformat= 'power',row=3, col=1)
fig.update_yaxes(title_text="Scaled Density", 
                  type="log", 
                 exponentformat= 'power',row=4, col=1)

# for month in month_list:

#     time_avg,Rho_x = orbit_avg_generic(models_dens[month+'Rho_x']['date'],
#                                             models_dens[month+'Rho_x']['Rho_x'],
#                                             models_dens[month+'Rho_x']['lat'])

#     time_avg,Rho_std = orbit_avg_generic(models_dens[month+'Rho_x']['date'],
#                                             models_dens[month+'Rho_x']['Rho_std'],
#                                             models_dens[month+'Rho_x']['lat'])


#     fig.add_trace(go.Scattergl(x=time_avg,
#                                y=Rho_x,
#                                ### name= model_m1,
#                                mode='markers+lines',
#                                opacity=1,
#                                marker=dict(color='black',size=5),
#                                    line = dict( dash ='solid', color = 'black', width=4),
#                                showlegend=False), row=3, col=1)
#     ## ERRROR BARS
#     fig.add_trace(go.Scattergl(x=time_avg,
#                                y=np.array(Rho_x)\
#                                    +np.array(Rho_std),
#                                ### name= model_m1,
#                                mode='lines',
#                                opacity=.8,
#                                    line = dict( dash ='dash', color = 'grey', width=3),
#                                showlegend=False), row=3, col=1)
#     fig.add_trace(go.Scattergl(x=time_avg,
#                                y=np.array(Rho_x)\
#                                   -np.array(Rho_std),
#                                ### name= model_m1,
#                                mode='lines',
#                                opacity=.8,
#                                    line = dict( dash ='dash', color = 'grey', width=3),
#                                showlegend=False), row=3, col=1)

    

    
a='input'
# s=settings_spire
fig.update_layout(#title=f"Spire FM{SAT}, Orbit Fit with {s['hours_between_cd_adj'][a]}-hr Scaling Factors", 
#                   title=f"{s['cd_model'][a]}, {s['hours_between_cd_adj'][a]}-hr Scale from CD={s['cd_value'][a]}", 
                  autosize=False,    width=850,    height=900,
                  legend= {'itemsizing': 'trace'},
                  font=font_dict,
                  plot_bgcolor='white', 
                 )
fig.update_annotations(font_size=16)  # Increase size of subplot title
# fig.show(config=config)
fig.show(config= dict({
                'displayModeBar': False,
                'responsive': True,
                'staticPlot': False,
                'displaylogo': False,
                'showTips': False,
                }),
#          renderer='jpg',
)


